In [139]:
"""PROJECT 3

PAGES TO SCRAP :

Main page of all genres : 1 page

Fantasy, Fantastique et bit-lit: 16 pages
Thriller, polar, aventure et horreur: 17 pages
Jeunesse et Young Adult: 21 pages
Contemporaine: 14 pages
Classique, théâtre, poésie, nouvelles: 4 pages
Science-Fiction: 5 pages
Historique: 6 pages
Romances: 8 pages
Non-fiction: 4 pages
BDs, Comics et Mangas: 7 pages
Enfants (pour les plus petits et leurs parents): 3 pages
TOTAL : 105

With ~30 books per page => 2 930

Comment analysis :

Comments : ~95 000
Page Comments : ~9 500

Unique Profils : 77 000 inscris, 

WORKFLOW:
1) Get the first link
2) get the pagination settings
3) Create a function that will read your soup and get the links for objects
4) Gather all the pages to get all the link to all objects
5) Create a function  that will read the soup of the object and collect all necessary information
6) Return your data into a df,csv,sql,db

REMINDERS
#Create a random sleep (1-5 s) for random number of pages (5-10)
#Use 'Task schuduler' to create task and run your script like twice a month 

CHALLENGES :
- Improve skills with Dict, pandas and SQL
- Deal with pages url and [..] in the pages indentation
- Deal with pages inside pages inside pages 
- Deal with pages without pagination
- Uge amount of data
- Extract every post with only pseudo, profil link and all the text using Regex

Hours :
- Jeudi : 5h
- Vendredi : 3h + 3h (end of all the scrapping code)+ (from 19h => put lst and dict into df)
- Samedi : put df into mysql, use API AI to analyze text
- Dimanche : build an user interface to 'play'
"""

"PROJECT 3\n\nPAGES TO SCRAP :\n\nMain page of all genres : 1 page\n\nFantasy, Fantastique et bit-lit: 16 pages\nThriller, polar, aventure et horreur: 17 pages\nJeunesse et Young Adult: 21 pages\nContemporaine: 14 pages\nClassique, théâtre, poésie, nouvelles: 4 pages\nScience-Fiction: 5 pages\nHistorique: 6 pages\nRomances: 8 pages\nNon-fiction: 4 pages\nBDs, Comics et Mangas: 7 pages\nEnfants (pour les plus petits et leurs parents): 3 pages\nTOTAL : 105\n\nWith ~30 books per page => 2 930\n\nComment analysis :\n\nProfil page : ~95 000\n\nWORKFLOW:\n1) Get the first link\n2) get the pagination settings\n3) Create a function that will read your soup and get the links for objects\n4) Gather all the pages to get all the link to all objects\n5) Create a function  that will read the soup of the object and collect all necessary information\n6) Return your data into a df,csv,sql,db\n\nREMINDERS\n#Create a random sleep (1-5 s) for random number of pages (5-10)\n#Use 'Task schuduler' to create 

In [596]:
#GO GO GO

In [597]:
#My request Header to be polite and optimise my chance to not be blocked
#No APIs it's an HTML / CSS website

headers = """Accept: image/webp,image/apng,image/*,*/*;q=0.8
Accept-Encoding: gzip, deflate, br
Accept-Language: fr-FR,fr;q=0.9,en-US;q=0.8,en;q=0.7
Cache-Control: no-cache
Connection: keep-alive
Cookie: PHPSESSID=t823a14605h1kughn38jeee3eh; __utma=193597488.1766116086.1586421513.1586421513.1586421513.1; __utmc=193597488; __utmz=193597488.1586421513.1.1.utmcsr=google|utmccn=(organic)|utmcmd=organic|utmctr=(not%20provided); cookieconsent_status=dismiss; __utmt=1; __utmb=193597488.87.10.1586421513
Host: www.livraddict.com
Pragma: no-cache
Referer: https://www.livraddict.com/forum/viewforum.php?p=2&id=19
Sec-Fetch-Dest: image
Sec-Fetch-Mode: no-cors
Sec-Fetch-Site: same-origin
User-Agent: Mozilla/5.0 (Macintosh; Intel Mac OS X 10_14_5) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/80.0.3987.149 Safari/537.36"""


In [598]:
import requests as r
import random
import re
import time
import pandas as pd
import numpy as np
import pandas as pd
import pymysql
import json
from bs4 import BeautifulSoup
from sqlalchemy import create_engine
from ibm_watson import ToneAnalyzerV3
from ibm_cloud_sdk_core.authenticators import IAMAuthenticator
#from aylienapiclient import textapi - useless because no french

headers = dict([i.split(': ') for i in headers.split('\n')])

url = 'https://www.livraddict.com/forum/viewcategory.php?id=4'
html=r.get(url, headers=headers).content
soup=BeautifulSoup(html)

In [601]:
# Connect to our Rocambole SQL database on Sequel Pro
username='root'
password = 'toto'
host='localhost'
database='Rocambole'

engine=create_engine(f'mysql+pymysql://{username}:{password}@{host}/{database}')


In [600]:
#IBM Ton Analyzer 

"""Tons 2017-09-21: The service can return results for the following tone IDs: 
- anger,
- fear, 
- joy, 
- and sadness (emotional tones); 

- analytical,
- confident, 
- and tentative (language tones). 

The service returns results only for tones whose scores meet a minimum threshold of 0.5."""

'Tons 2017-09-21: The service can return results for the following tone IDs: \n- anger,\n- fear, \n- joy, and sadness (emotional tones); analytical, confident, and tentative (language tones). \n\nThe service returns results only for tones whose scores meet a minimum threshold of 0.5.'

In [602]:
# Connect to our API IBM Ton Analyzer
authenticator = IAMAuthenticator('ycME6ijTAo4fgzsO36NyEXDPdpH4ACbUzunDhpSgAjy0')
tone_analyzer = ToneAnalyzerV3(
    version='2017-09-21',
    authenticator=authenticator
)
tone_analyzer.set_service_url('https://api.eu-gb.tone-analyzer.watson.cloud.ibm.com/instances/d1da191f-19fe-4af2-b416-4d6da5a96337')


In [603]:
#Task : get all the genre and their page link
#CSS selector : h3>a

all_genres = {i.text.strip():['https://www.livraddict.com/forum/'+i['href']] for i in soup.select('h3>a')}
all_genres



{'Fantasy, Fantastique et bit-lit': ['https://www.livraddict.com/forum/viewforum.php?id=17'],
 'Thriller, polar, aventure et horreur': ['https://www.livraddict.com/forum/viewforum.php?id=19'],
 'Jeunesse et Young Adult': ['https://www.livraddict.com/forum/viewforum.php?id=20'],
 'Contemporaine': ['https://www.livraddict.com/forum/viewforum.php?id=16'],
 'Classique, théâtre, poésie, nouvelles': ['https://www.livraddict.com/forum/viewforum.php?id=15'],
 'Science-Fiction': ['https://www.livraddict.com/forum/viewforum.php?id=18'],
 'Historique': ['https://www.livraddict.com/forum/viewforum.php?id=41'],
 'Romances': ['https://www.livraddict.com/forum/viewforum.php?id=14'],
 'Non-fiction': ['https://www.livraddict.com/forum/viewforum.php?id=22'],
 'BDs, Comics et Mangas': ['https://www.livraddict.com/forum/viewforum.php?id=30'],
 'Enfants (pour les plus petits et leurs parents)': ['https://www.livraddict.com/forum/viewforum.php?id=62']}

In [604]:
#Task : get and add the last comment per genre into our dict all_genres
#CSS selector : .last_message >a

i=0
for x in all_genres.values():
    x.append([i.text.strip() for i in soup.select('.last_message >a')][i])

all_genres

{'Fantasy, Fantastique et bit-lit': ['https://www.livraddict.com/forum/viewforum.php?id=17',
  '10 avril 2020 14:09:03'],
 'Thriller, polar, aventure et horreur': ['https://www.livraddict.com/forum/viewforum.php?id=19',
  '10 avril 2020 14:09:03'],
 'Jeunesse et Young Adult': ['https://www.livraddict.com/forum/viewforum.php?id=20',
  '10 avril 2020 14:09:03'],
 'Contemporaine': ['https://www.livraddict.com/forum/viewforum.php?id=16',
  '10 avril 2020 14:09:03'],
 'Classique, théâtre, poésie, nouvelles': ['https://www.livraddict.com/forum/viewforum.php?id=15',
  '10 avril 2020 14:09:03'],
 'Science-Fiction': ['https://www.livraddict.com/forum/viewforum.php?id=18',
  '10 avril 2020 14:09:03'],
 'Historique': ['https://www.livraddict.com/forum/viewforum.php?id=41',
  '10 avril 2020 14:09:03'],
 'Romances': ['https://www.livraddict.com/forum/viewforum.php?id=14',
  '10 avril 2020 14:09:03'],
 'Non-fiction': ['https://www.livraddict.com/forum/viewforum.php?id=22',
  '10 avril 2020 14:09:03'

In [605]:
#add a list element in values of each genre in all_genres with the url of all the pages per genre

for value in all_genres.values():
    url = value[0]
    html=r.get(url, headers=headers).content
    soup=BeautifulSoup(html)
    value.append(int([last_page.text for last_page in soup.select('.pagination li')][-1]))
        
all_genres

{'Fantasy, Fantastique et bit-lit': ['https://www.livraddict.com/forum/viewforum.php?id=17',
  '10 avril 2020 14:09:03',
  16],
 'Thriller, polar, aventure et horreur': ['https://www.livraddict.com/forum/viewforum.php?id=19',
  '10 avril 2020 14:09:03',
  17],
 'Jeunesse et Young Adult': ['https://www.livraddict.com/forum/viewforum.php?id=20',
  '10 avril 2020 14:09:03',
  21],
 'Contemporaine': ['https://www.livraddict.com/forum/viewforum.php?id=16',
  '10 avril 2020 14:09:03',
  14],
 'Classique, théâtre, poésie, nouvelles': ['https://www.livraddict.com/forum/viewforum.php?id=15',
  '10 avril 2020 14:09:03',
  4],
 'Science-Fiction': ['https://www.livraddict.com/forum/viewforum.php?id=18',
  '10 avril 2020 14:09:03',
  5],
 'Historique': ['https://www.livraddict.com/forum/viewforum.php?id=41',
  '10 avril 2020 14:09:03',
  6],
 'Romances': ['https://www.livraddict.com/forum/viewforum.php?id=14',
  '10 avril 2020 14:09:03',
  8],
 'Non-fiction': ['https://www.livraddict.com/forum/view

In [606]:
#Transform le Dict all_genres into DataFrame => df_all_genres BEFORE adding all links

df_characteristics_of_all_genres = pd.DataFrame.from_dict(all_genres, orient='index')
df_characteristics_of_all_genres = df_characteristics_of_all_genres.reset_index()
df_characteristics_of_all_genres = df_characteristics_of_all_genres.rename(columns={'index':'Genre',0:'Main URL of the Genre',1:'Last Update',2:'Nb of pages'})



In [607]:
#Add df_all_genres (without all links pages per genre) to MySQL
df_characteristics_of_all_genres.to_sql('df_characteristics_of_all_genres', engine, if_exists='replace', index=True)




In [608]:
#add all the url links of all the pages of books per genre

#TO DO : add # of books per genre ! 

for value in all_genres.values():
    max_pages = value[2]
    base_url=value[0].split('?')[0]
    id_genre_url = value[0].split('?')[1]
    
    for x in range(max_pages):
        value.append(base_url+'?p='+str(x+1)+"&"+id_genre_url)

all_genres

{'Fantasy, Fantastique et bit-lit': ['https://www.livraddict.com/forum/viewforum.php?id=17',
  '10 avril 2020 14:09:03',
  16,
  'https://www.livraddict.com/forum/viewforum.php?p=1&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=2&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=3&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=4&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=5&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=6&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=7&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=8&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=9&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=10&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=11&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=12&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=13&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=14&id=17',


In [609]:
#Task : create a dict with the genre and all its url pages
#CSS selector : h3>a

url = 'https://www.livraddict.com/forum/viewcategory.php?id=4'
html=r.get(url, headers=headers).content
soup=BeautifulSoup(html)
lst_of_url_per_genre = {i.text.strip():[] for i in soup.select('h3>a')}

for x,y in all_genres.items():
    lst = []
    
    for i in range(3,len(y)):
        lst.append(y[i])
        lst_of_url_per_genre[x] = lst

lst_of_url_per_genre

{'Fantasy, Fantastique et bit-lit': ['https://www.livraddict.com/forum/viewforum.php?p=1&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=2&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=3&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=4&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=5&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=6&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=7&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=8&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=9&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=10&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=11&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=12&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=13&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=14&id=17',
  'https://www.livraddict.com/forum/viewforum.php?p=15&id=17',
  'https://www.livraddict.com

In [610]:
#WARNING => 5 min RUN (count untill 105 with 2 sec break)
#Task : get title of EACH page
#CSS selector : .tclcon a:first-child

genres_book_bookurl= []

count = 0

for x,y in lst_of_url_per_genre.items():
    
    for i in range(len(y)):
        url = y[i]
        html=r.get(url, headers=headers).content
        soup=BeautifulSoup(html)
        genres_book_bookurl.append([x,{i.text.strip():'https://www.livraddict.com/forum/'+i['href'] for i in soup.select('.tclcon a:first-child')}])
        count += 1
        print(count)
        time.sleep(2)

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105


In [611]:
genres_book_bookurl

[['Fantasy, Fantastique et bit-lit',
  {'[Sapkowski, Andrzej] Sorceleur - Saga': 'https://www.livraddict.com/forum/viewtopic.php?id=11245',
   "[Ivy, Alexandra] Les Gardiens de l'éternité - Saga": 'https://www.livraddict.com/forum/viewtopic.php?id=6863',
   '[Feist, Raymond E.] La Guerre de la Faille - Saga': 'https://www.livraddict.com/forum/viewtopic.php?id=12385',
   "[Goddyn, Régis] L'Ensorceleur des choses menues": 'https://www.livraddict.com/forum/viewtopic.php?id=32738',
   '[Pacat, S.C] Prince Captif - Saga': 'https://www.livraddict.com/forum/viewtopic.php?id=20616',
   '[Caldera, Georgia] Les Larmes rouges - Saga': 'https://www.livraddict.com/forum/viewtopic.php?id=20015',
   "Qu'est-ce qui ferait le jeu fantastique parfait pour vous?": 'https://www.livraddict.com/forum/viewtopic.php?id=32714',
   'À propos du Doom of Mandos': 'https://www.livraddict.com/forum/viewtopic.php?id=32701',
   '[Frost, Jeaniene] Chasseuse de la nuit - Saga': 'https://www.livraddict.com/forum/viewtop

In [612]:
#Transform the list of list of dict Book:url per genre into one dict_of_all_books_per_genre { genre_1 : [all books_genre_1]}

dict_of_all_books_per_genre = {}
previous = genres_book_bookurl[0][0]
lst_to_add = []

for genre, book_and_url in genres_book_bookurl:
        
    for book in book_and_url :
        
        ongoing = genre
        
        if previous == ongoing:
            
            lst_to_add.append(book)
    
        else : 
            lst_to_add = []
            lst_to_add.append(book)

        dict_of_all_books_per_genre[genre] = lst_to_add
        previous = genre

dict_of_all_books_per_genre

{'Fantasy, Fantastique et bit-lit': ['[Sapkowski, Andrzej] Sorceleur - Saga',
  "[Ivy, Alexandra] Les Gardiens de l'éternité - Saga",
  '[Feist, Raymond E.] La Guerre de la Faille - Saga',
  "[Goddyn, Régis] L'Ensorceleur des choses menues",
  '[Pacat, S.C] Prince Captif - Saga',
  '[Caldera, Georgia] Les Larmes rouges - Saga',
  "Qu'est-ce qui ferait le jeu fantastique parfait pour vous?",
  'À propos du Doom of Mandos',
  '[Frost, Jeaniene] Chasseuse de la nuit - Saga',
  "[Goodkind, Terry] L'Épée de Vérité - Saga",
  "[Bry, David] Que passe l'hiver",
  '[Latil-Nicolas, Thibaud] Chevauche-brumes - Saga',
  '[Brooks, Terry] Shannara - Saga',
  '[Tolkien, J. R. R.] Le Seigneur des Anneaux - Saga',
  '[Erikson, Steven] Le Livre malazéen des glorieux défunts - Saga',
  '[Carey, Jacqueline] Kushiel',
  '[Briggs, Patricia] Alpha et Omega - Saga',
  '[Elfydil] Le clan du corbeau blanc - Saga',
  '[Jemisin, N.K.] Les Livres de la Terre Fracturée - Saga',
  "[Jemisin, N.K.] La Trilogie de L'H

In [613]:
#Transform the dict_of_all_books_per_genre into DataFrame => df_of_all_books_per_genre

df_all_books_per_genre = pd.DataFrame.from_dict(dict_of_all_books_per_genre, orient='index').T
df_all_books_per_genre

Fantasy, Fantastique et bit-lit  \
0                [Sapkowski, Andrzej] Sorceleur - Saga   
1    [Ivy, Alexandra] Les Gardiens de l'éternité - ...   
2    [Feist, Raymond E.] La Guerre de la Faille - Saga   
3      [Goddyn, Régis] L'Ensorceleur des choses menues   
4                    [Pacat, S.C] Prince Captif - Saga   
..                                                 ...   
589                                               None   
590                                               None   
591                                               None   
592                                               None   
593                                               None   

                  Thriller, polar, aventure et horreur  \
0                           [Thilliez, Franck] Vertige   
1                               Ils ont rencontré John   
2                              Les assassins innocents   
3    [Chapman Julia] Les détectives du Yorkshire - ...   
4             [Giebel, Karine]Purgatoire des innocents   
..                                                 ...   
589                                               None   
590                                               None   
591                                               None   
592                                               None   
593                                               None   

                               Jeunesse et Young Adult  \
0    [Montgomery, Lucy Maud] Anne... la maison aux ...   
1                 [Murail, Marie-Aude] Sauveur et Fils   
2     [Brashares, Ann] Quatre filles et un jean - Saga   
3          [Meyer, Marissa] Chroniques Lunaires - saga   
4      [Maas, Sarah J.] Keleana, l'Assassineuse - Saga   
..                                                 ...   
589             [Belfiore, Robert] Les écrans de Brume   
590               [Barker, Clive] Le Voleur d'Éternité   
591              [Kérillis, Hélène] Le Cheval De Troie   
592          [Benchetrit, André] Vendeur de cauchemars   
593                [Chabas, Jean-François] Les lionnes   

                                      Contemporaine  \
0                           [Faye, Gaël] Petit pays   
1    [Hirigoyen, Marie-France] Le Harcèlement Moral   
2       [Constantine, Barbara] Et puis, Paulette...   
3                     [Schlink, Bernhard] Le liseur   
4              [Ferrante, Elena] L'amie prodigieuse   
..                                              ...   
589                                            None   
590                                            None   
591                                            None   
592                                            None   
593                                            None   

                 Classique, théâtre, poésie, nouvelles  \
0             [Zola, Emile] Les Rougon Macquart - Saga   
1                   [Austen, Jane] Orgueil et Préjugés   
2       [Proust, Marcel] A la recherche du temps perdu   
3     [Fitzgerald, Francis Scott] Gatsby le Magnifique   
4    [Choderlos De Laclos, Pierre] Les Liaisons Dan...   
..                                                 ...   
589                                               None   
590                                               None   
591                                               None   
592                                               None   
593                                               None   

                          Science-Fiction  \
0    [Clavel, Fabien] Feuillets de cuivre   
1                  [K. Dick, Philip] Ubik   
2    [Wilson, Robert Charles] Spin - Saga   
3      [Werber, Bernard] Demain les chats   
4              [Weir, Andy] Seul sur Mars   
..                                    ...   
589                                  None   
590                                  None   
591                                  None   
592                                  None   
593                                  None   

                                 

In [625]:
#Add df_all_books_and_links_per_genre to MySQL
df_all_books_per_genre.to_sql('df_all_books_per_genre', engine, if_exists='replace', index=True)





In [615]:
#WARNING => LONG RUN untill 2930 (~10min with 1 to 3 sec time sleep)
#Create a dict with all the books and all the url pages

dict_book_all_url_pages = {}
print(dict_book_all_url_pages)
count = 0

for genre_with_books in genres_book_bookurl:
    
    for j, h in genre_with_books[1].items():
        
        url = h
        html=r.get(url, headers=headers).content
        soup=BeautifulSoup(html)
        
        if soup.select('.pagination li'):
            
            max_pages = int([last_page.text for last_page in soup.select('.pagination li')[-1]][0])
            base_url = h.split('?')[0]
            id_genre_url = h.split('?')[1]
            dict_book_all_url_pages[j]=[]
            
            for all_pages in range(max_pages):
                
                dict_book_all_url_pages[j].append(base_url+'?p='+str(all_pages+1)+"&"+id_genre_url)
            
        else :
            dict_book_all_url_pages[j]=[url]
    
        count += 1
        print(count)
    
    print('sleep')
    time.sleep(random.randint(1, 3))
    print('end_sleep')
        
print(dict_book_all_url_pages)


{}
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
sleep
end_sleep
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
sleep
end_sleep
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
sleep
end_sleep
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
sleep
end_sleep
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
sleep
end_sleep
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
sleep
end_sleep
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
sleep
end_sleep
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
sleep
end_sleep
239
240
241
242
243
244
2

1678
sleep
end_sleep
1679
1680
1681
1682
1683
1684
1685
1686
1687
1688
1689
1690
1691
1692
1693
1694
1695
1696
1697
1698
1699
1700
1701
1702
1703
1704
1705
1706
1707
1708
sleep
end_sleep
1709
1710
1711
1712
1713
1714
1715
1716
1717
1718
1719
1720
1721
1722
1723
1724
1725
1726
1727
1728
1729
1730
1731
1732
1733
1734
1735
1736
1737
1738
sleep
end_sleep
1739
1740
1741
1742
1743
1744
1745
1746
1747
1748
1749
1750
1751
1752
1753
1754
1755
1756
1757
1758
1759
1760
1761
1762
1763
1764
1765
1766
1767
1768
sleep
end_sleep
1769
1770
1771
1772
1773
1774
1775
1776
1777
1778
1779
1780
1781
1782
1783
1784
1785
1786
1787
1788
1789
1790
1791
1792
1793
1794
1795
1796
1797
1798
sleep
end_sleep
1799
1800
1801
1802
1803
1804
1805
1806
1807
1808
1809
1810
1811
1812
1813
1814
1815
1816
1817
1818
1819
1820
1821
1822
1823
1824
1825
1826
1827
1828
sleep
end_sleep
1829
1830
1831
1832
1833
1834
1835
1836
1837
1838
1839
1840
1841
1842
1843
1844
1845
1846
1847
1848
1849
1850
1851
1852
1853
1854
1855
1856
1857
1858

In [683]:
#WARNING => LONG RUN untill ~11 000 (~120min with 1 to 3 sec time sleep)

#Create a Dict with all the comments with pseudo and links per book {Book:{Pseudo{lien:comment}}} by using dict_book_all_url_pages

#CSS Selector for post bloc post odd => .blockpost.rowodd
#CSS Selector for post bloc post odd => .blockpost.roweven
#CSS Selector for user name and profil link => .blockpost.rowodd .post_username>a
#CSS Selector for user post => .blockpost.rowodd .post_message_content

#Pattern => 'href="\/profil.*?<strong>.*?<\/strong>'
#Pattern => 'href="\/profil.*?"'
#Pattern => '<.*?>'

lst_of_userprofil_url = []
count = 0

dict_book_pseudo_lien_and_comments = {}

for x,y in dict_book_all_url_pages.items():
    
    lst_to_add= []
    
    for i in range(len(y)):
        url = y[i]
        print('url',url)
        html=r.get(url, headers=headers).content
        soup=BeautifulSoup(html)
        
        nb_of_posts = [post for post in soup.select('.blockpost')]
        
        for i in nb_of_posts:
            
            pattern_1 = 'href="/profil.*?<strong>.*?<\/strong>'
            pattern_2 = 'href="\/profil.*?"'
            pattern_3 = '<.*?>'
            
            #Clean post_username
            post_username = re.findall(pattern_1, str(i))
            post_username = post_username[0].split('>')
            post_username = post_username[2].split('<')
            post_username = post_username[0]
            
            #Clean post_userprofil_link
            post_userprofil_link = re.findall(pattern_2, str(i))
            post_userprofil_link = post_userprofil_link[0].split('"')
            post_userprofil_link = 'https://www.livraddict.com' + post_userprofil_link[1]
            #Store all user profiles url
            lst_of_userprofil_url.append(post_userprofil_link)
            
            #Clean post_user
            post_user = re.split(pattern_3, str(i))
            post_user = ''.join(post_user)
            post_user = post_user.split('\n')
            post_user = ''.join(post_user)
            
            lst_to_add.append([post_username,post_userprofil_link,post_user])
    
            dict_book_pseudo_lien_and_comments[x] = lst_to_add

    count += 1
    print(count)
    
    print('sleep')
    time.sleep(random.randint(1, 3))
    print('end_sleep')
            



url https://www.livraddict.com/forum/viewtopic.php?p=1&id=11245


DONALD {'[Sapkowski, Andrzej] Sorceleur - Saga': [['Le Serial Lecteur', 'https://www.livraddict.com/profil/leseriallecteur/', ' Le Serial Lecteur Livraddictien débutantHors ligne#1 29 Mai 2012 20:43:08&lt;image&gt;Geralt de Riv est un personnage étrange, une bizarrerie de la nature, un mutant qui, grâce à la magie et à un long entraînement, mais aussi grâce à un mystérieux élixir, est devenu un meurtrier parfait. Ses cheveux blancs, ses yeux nyctalopes et son manteau noir effrayent et fascinent. Il parcourt des contrées pittoresques en gagnant sa vie comme chasseur de monstres. En ces temps obscurs, ogres, goules et vampires pullulent, et les magiciens sont des manipulateurs experts. Contre ces menaces, il faut un tueur à gages à la hauteur. Car Geralt est plus qu’un guerrier ou un mage. C’est un Sorceleur. Il est unique. Au cours de ses aventures, il rencontrera une autoritaire mais généreuse prêtresse, un troubadour pa

end_sleep
url https://www.livraddict.com/forum/viewtopic.php?p=1&id=6863


DONALD {'[Sapkowski, Andrzej] Sorceleur - Saga': [['Le Serial Lecteur', 'https://www.livraddict.com/profil/leseriallecteur/', ' Le Serial Lecteur Livraddictien débutantHors ligne#1 29 Mai 2012 20:43:08&lt;image&gt;Geralt de Riv est un personnage étrange, une bizarrerie de la nature, un mutant qui, grâce à la magie et à un long entraînement, mais aussi grâce à un mystérieux élixir, est devenu un meurtrier parfait. Ses cheveux blancs, ses yeux nyctalopes et son manteau noir effrayent et fascinent. Il parcourt des contrées pittoresques en gagnant sa vie comme chasseur de monstres. En ces temps obscurs, ogres, goules et vampires pullulent, et les magiciens sont des manipulateurs experts. Contre ces menaces, il faut un tueur à gages à la hauteur. Car Geralt est plus qu’un guerrier ou un mage. C’est un Sorceleur. Il est unique. Au cours de ses aventures, il rencontrera une autoritaire mais généreuse prêtresse, un trou



DONALD {'[Sapkowski, Andrzej] Sorceleur - Saga': [['Le Serial Lecteur', 'https://www.livraddict.com/profil/leseriallecteur/', ' Le Serial Lecteur Livraddictien débutantHors ligne#1 29 Mai 2012 20:43:08&lt;image&gt;Geralt de Riv est un personnage étrange, une bizarrerie de la nature, un mutant qui, grâce à la magie et à un long entraînement, mais aussi grâce à un mystérieux élixir, est devenu un meurtrier parfait. Ses cheveux blancs, ses yeux nyctalopes et son manteau noir effrayent et fascinent. Il parcourt des contrées pittoresques en gagnant sa vie comme chasseur de monstres. En ces temps obscurs, ogres, goules et vampires pullulent, et les magiciens sont des manipulateurs experts. Contre ces menaces, il faut un tueur à gages à la hauteur. Car Geralt est plus qu’un guerrier ou un mage. C’est un Sorceleur. Il est unique. Au cours de ses aventures, il rencontrera une autoritaire mais généreuse prêtresse, un troubadour paillard au grand cœur, et une magicienne capricieuse aux charmes 



DONALD {'[Sapkowski, Andrzej] Sorceleur - Saga': [['Le Serial Lecteur', 'https://www.livraddict.com/profil/leseriallecteur/', ' Le Serial Lecteur Livraddictien débutantHors ligne#1 29 Mai 2012 20:43:08&lt;image&gt;Geralt de Riv est un personnage étrange, une bizarrerie de la nature, un mutant qui, grâce à la magie et à un long entraînement, mais aussi grâce à un mystérieux élixir, est devenu un meurtrier parfait. Ses cheveux blancs, ses yeux nyctalopes et son manteau noir effrayent et fascinent. Il parcourt des contrées pittoresques en gagnant sa vie comme chasseur de monstres. En ces temps obscurs, ogres, goules et vampires pullulent, et les magiciens sont des manipulateurs experts. Contre ces menaces, il faut un tueur à gages à la hauteur. Car Geralt est plus qu’un guerrier ou un mage. C’est un Sorceleur. Il est unique. Au cours de ses aventures, il rencontrera une autoritaire mais généreuse prêtresse, un troubadour paillard au grand cœur, et une magicienne capricieuse aux charmes 



DONALD {'[Sapkowski, Andrzej] Sorceleur - Saga': [['Le Serial Lecteur', 'https://www.livraddict.com/profil/leseriallecteur/', ' Le Serial Lecteur Livraddictien débutantHors ligne#1 29 Mai 2012 20:43:08&lt;image&gt;Geralt de Riv est un personnage étrange, une bizarrerie de la nature, un mutant qui, grâce à la magie et à un long entraînement, mais aussi grâce à un mystérieux élixir, est devenu un meurtrier parfait. Ses cheveux blancs, ses yeux nyctalopes et son manteau noir effrayent et fascinent. Il parcourt des contrées pittoresques en gagnant sa vie comme chasseur de monstres. En ces temps obscurs, ogres, goules et vampires pullulent, et les magiciens sont des manipulateurs experts. Contre ces menaces, il faut un tueur à gages à la hauteur. Car Geralt est plus qu’un guerrier ou un mage. C’est un Sorceleur. Il est unique. Au cours de ses aventures, il rencontrera une autoritaire mais généreuse prêtresse, un troubadour paillard au grand cœur, et une magicienne capricieuse aux charmes 



DONALD {'[Sapkowski, Andrzej] Sorceleur - Saga': [['Le Serial Lecteur', 'https://www.livraddict.com/profil/leseriallecteur/', ' Le Serial Lecteur Livraddictien débutantHors ligne#1 29 Mai 2012 20:43:08&lt;image&gt;Geralt de Riv est un personnage étrange, une bizarrerie de la nature, un mutant qui, grâce à la magie et à un long entraînement, mais aussi grâce à un mystérieux élixir, est devenu un meurtrier parfait. Ses cheveux blancs, ses yeux nyctalopes et son manteau noir effrayent et fascinent. Il parcourt des contrées pittoresques en gagnant sa vie comme chasseur de monstres. En ces temps obscurs, ogres, goules et vampires pullulent, et les magiciens sont des manipulateurs experts. Contre ces menaces, il faut un tueur à gages à la hauteur. Car Geralt est plus qu’un guerrier ou un mage. C’est un Sorceleur. Il est unique. Au cours de ses aventures, il rencontrera une autoritaire mais généreuse prêtresse, un troubadour paillard au grand cœur, et une magicienne capricieuse aux charmes 



DONALD {'[Sapkowski, Andrzej] Sorceleur - Saga': [['Le Serial Lecteur', 'https://www.livraddict.com/profil/leseriallecteur/', ' Le Serial Lecteur Livraddictien débutantHors ligne#1 29 Mai 2012 20:43:08&lt;image&gt;Geralt de Riv est un personnage étrange, une bizarrerie de la nature, un mutant qui, grâce à la magie et à un long entraînement, mais aussi grâce à un mystérieux élixir, est devenu un meurtrier parfait. Ses cheveux blancs, ses yeux nyctalopes et son manteau noir effrayent et fascinent. Il parcourt des contrées pittoresques en gagnant sa vie comme chasseur de monstres. En ces temps obscurs, ogres, goules et vampires pullulent, et les magiciens sont des manipulateurs experts. Contre ces menaces, il faut un tueur à gages à la hauteur. Car Geralt est plus qu’un guerrier ou un mage. C’est un Sorceleur. Il est unique. Au cours de ses aventures, il rencontrera une autoritaire mais généreuse prêtresse, un troubadour paillard au grand cœur, et une magicienne capricieuse aux charmes 



DONALD {'[Sapkowski, Andrzej] Sorceleur - Saga': [['Le Serial Lecteur', 'https://www.livraddict.com/profil/leseriallecteur/', ' Le Serial Lecteur Livraddictien débutantHors ligne#1 29 Mai 2012 20:43:08&lt;image&gt;Geralt de Riv est un personnage étrange, une bizarrerie de la nature, un mutant qui, grâce à la magie et à un long entraînement, mais aussi grâce à un mystérieux élixir, est devenu un meurtrier parfait. Ses cheveux blancs, ses yeux nyctalopes et son manteau noir effrayent et fascinent. Il parcourt des contrées pittoresques en gagnant sa vie comme chasseur de monstres. En ces temps obscurs, ogres, goules et vampires pullulent, et les magiciens sont des manipulateurs experts. Contre ces menaces, il faut un tueur à gages à la hauteur. Car Geralt est plus qu’un guerrier ou un mage. C’est un Sorceleur. Il est unique. Au cours de ses aventures, il rencontrera une autoritaire mais généreuse prêtresse, un troubadour paillard au grand cœur, et une magicienne capricieuse aux charmes 



DONALD {'[Sapkowski, Andrzej] Sorceleur - Saga': [['Le Serial Lecteur', 'https://www.livraddict.com/profil/leseriallecteur/', ' Le Serial Lecteur Livraddictien débutantHors ligne#1 29 Mai 2012 20:43:08&lt;image&gt;Geralt de Riv est un personnage étrange, une bizarrerie de la nature, un mutant qui, grâce à la magie et à un long entraînement, mais aussi grâce à un mystérieux élixir, est devenu un meurtrier parfait. Ses cheveux blancs, ses yeux nyctalopes et son manteau noir effrayent et fascinent. Il parcourt des contrées pittoresques en gagnant sa vie comme chasseur de monstres. En ces temps obscurs, ogres, goules et vampires pullulent, et les magiciens sont des manipulateurs experts. Contre ces menaces, il faut un tueur à gages à la hauteur. Car Geralt est plus qu’un guerrier ou un mage. C’est un Sorceleur. Il est unique. Au cours de ses aventures, il rencontrera une autoritaire mais généreuse prêtresse, un troubadour paillard au grand cœur, et une magicienne capricieuse aux charmes 

KeyboardInterrupt: 

In [685]:
#check
print(dict_book_pseudo_lien_and_comments["[Ivy, Alexandra] Les Gardiens de l'éternité - Saga"]) 
                                         

[['Nastasia', 'https://www.livraddict.com/profil/nastasia/', " Nastasia Commence à sentir l encre qui colle aux doigtsHors ligne#1 30 Avril 2011 17:15:50&lt;image&gt;Voici une nouvelle saga dont le premier tome, intitulé Dante est sorti chez Milady le 22 avril dernier.Résumé du premier tome:Ce fut une journée chargée pour Abby Barlow. Dans à peine quelques heures, elle a survécu à une explosion, vu son employeur mourir, a fait un rêve saisissant et maintenant elle se trouve dans un hôtel miteux avec le sexy et suréel Dante, un homme qu'elle désire et craint. Depuis 341 ans, Dante est gardien auprès du Calice, une humaine choisie pour retenir la pénombre. Un terrible coup du sort a décidé qu'Abby serait dorénavant cette femme. Trois heures plus tôt, Dante aurait usé de tous ses charmes pour la séduire. Maintenant, son rôle est de la protéger. Et il en sera ainsi jusqu'à sa propre mort. Un plan terrifiant est en marche, un plan qui va plonger Dante et Abby au cœur d'une bataille épique e

In [618]:
#Transform the dict_book_pseudo_lien_and_comments into DataFrame => df_dict_book_pseudo_lien_and_comments

df_dict_book_pseudo_lien_and_comments = pd.DataFrame.from_dict(dict_book_pseudo_lien_and_comments, orient='index').T
df_dict_book_pseudo_lien_and_comments

[Sapkowski, Andrzej] Sorceleur - Saga  \
0      [Le Serial Lecteur, https://www.livraddict.com...   
1      [Walpurgis, https://www.livraddict.com/profil/...   
2      [Renan, https://www.livraddict.com/profil/rena...   
3      [Le Serial Lecteur, https://www.livraddict.com...   
4      [Vozrozhdenyie, https://www.livraddict.com/pro...   
...                                                  ...   
93208  [marieke, https://www.livraddict.com/profil/ma...   
93209  [Flof13, https://www.livraddict.com/profil/flo...   
93210  [marieke, https://www.livraddict.com/profil/ma...   
93211  [Invité, https://www.livraddict.com/profil/inv...   
93212  [chatperlipopette, https://www.livraddict.com/...   

      [Ivy, Alexandra] Les Gardiens de l'éternité - Saga  \
0      [Le Serial Lecteur, https://www.livraddict.com...   
1      [Walpurgis, https://www.livraddict.com/profil/...   
2      [Renan, https://www.livraddict.com/profil/rena...   
3      [Le Serial Lecteur, https://www.livraddict.com...   
4      [Vozrozhdenyie, https://www.livraddict.com/pro...   
...                                                  ...   
93208  [marieke, https://www.livraddict.com/profil/ma...   
93209  [Flof13, https://www.livraddict.com/profil/flo...   
93210  [marieke, https://www.livraddict.com/profil/ma...   
93211  [Invité, https://www.livraddict.com/profil/inv...   
93212  [chatperlipopette, https://www.livraddict.com/...   

       [Feist, Raymond E.] La Guerre de la Faille - Saga  \
0      [Le Serial Lecteur, https://www.livraddict.com...   
1      [Walpurgis, https://www.livraddict.com/profil/...   
2      [Renan, https://www.livraddict.com/profil/rena...   
3      [Le Serial Lecteur, https://www.livraddict.com...   
4      [Vozrozhdenyie, https://www.livraddict.com/pro...   
...                                                  ...   
93208  [marieke, https://www.livraddict.com/profil/ma...   
93209  [Flof13, https://www.livraddict.com/profil/flo...   
93210  [marieke, https://www.livraddict.com/profil/ma...   
93211  [Invité, https://www.livraddict.com/profil/inv...   
93212  [chatperlipopette, https://www.livraddict.com/...   

         [Goddyn, Régis] L'Ensorceleur des choses menues  \
0      [Le Serial Lecteur, https://www.livraddict.com...   
1      [Walpurgis, https://www.livraddict.com/profil/...   
2      [Renan, https://www.livraddict.com/profil/rena...   
3      [Le Serial Lecteur, https://www.livraddict.com...   
4      [Vozrozhdenyie, https://www.livraddict.com/pro...   
...                                                  ...   
93208  [marieke, https://www.livraddict.com/profil/ma...   
93209  [Flof13, https://www.livraddict.com/profil/flo...   
93210  [marieke, https://www.livraddict.com/profil/ma...   
93211  [Invité, https://www.livraddict.com/profil/inv...   
93212  [chatperlipopette, https://www.livraddict.com/...   

                       [Pacat, S.C] Prince Captif - Saga  \
0      [Le Serial Lecteur, https://www.livraddict.com...   
1      [Walpurgis, https://www.livraddict.com/profil/...   
2      [Renan, https://www.livraddict.com/profil/rena...   
3      [Le Serial Lecteur, https://www.livraddict.com...   
4      [Vozrozhdenyie, https://www.livraddict.com/pro...   
...                                                  ...   
93208  [marieke, https://www.livraddict.com/profil/ma...   
93209  [Flof13, https://www.livraddict.com/profil/flo...   
93210  [marieke, https://www.livraddict.com/profil/ma...   
93211  [Invité, https://www.livraddict.com/profil/inv...   
93212  [chatperlipopette, https://www.livraddict.com/...   

             [Caldera, Georgia] Les Larmes rouges - Saga  \
0      [Le Serial Lecteur, https://www.livraddict.com...   
1      [Walpurgis, https://www.livraddict.com/profil/...   
2      [Renan, https://www.livraddict.com/profil/rena...   
3      [Le Serial Lecteur, https://www.livraddict.com...   
4      [Vozrozhdenyie, https://www.livraddict.com/pro...   
...                                                  .

In [654]:
#WARNING => LONG RUN untill XXXX (~XXmin with 1 to 3 sec time sleep) - 1h pour 5 000 requests)

#dict_book_pseudo_lien_and_comments = {Book:{Pseudo{lien:comment}}}
#Transform dict_book_pseudo_lien_and_comments into dict_book_avis_per_pseudo by by calling an API
#dict_book_avis_per_pseudo = {Book:{Pseudo:avis}}}

#PROBLEME
review = 0
dict_book_avis_per_pseudo = {}
count = 0
lst_to_add = []

for x,y in dict_book_pseudo_lien_and_comments.items():
    
    for j in y :
        tone_id_to_add =[]
        comment_to_be_analyzed = j[2]
        tone_analysis = tone_analyzer.tone({'text': comment_to_be_analyzed},content_type='text/plain',content_language='fr').get_result()
        tone_analysis = json.dumps(tone_analysis, indent=1)
        dict_tone_analysis = json.loads(tone_analysis)
        dict_tone_analysis = dict_tone_analysis['document_tone']['tones']

        for tone_id in dict_tone_analysis:
            tone_id_to_add.append(tone_id['tone_id'])         
            lst_to_add.append([j[0],''.join(tone_id_to_add)])

        dict_book_avis_per_pseudo[x] = lst_to_add
        count += 1
        print(count)
    
    print('sleep')
    time.sleep(random.randint(1, 3))
    print('end_sleep')


ERROR:root:Forbidden
Traceback (most recent call last):
  File "/opt/anaconda3/lib/python3.7/site-packages/ibm_cloud_sdk_core/base_service.py", line 229, in send
    response.status_code, error_message, http_response=response)
ibm_cloud_sdk_core.api_exception.ApiException: Error: Forbidden, Code: 403


ApiException: Error: Forbidden, Code: 403

In [652]:
dict_book_avis_per_pseudo

{'[Sapkowski, Andrzej] Sorceleur - Saga': [['Le Serial Lecteur',
   ' Le Serial Lecteur Livraddictien débutantHors ligne#1 29 Mai 2012 20:43:08&lt;image&gt;Geralt de Riv est un personnage étrange, une bizarrerie de la nature, un mutant qui, grâce à la magie et à un long entraînement, mais aussi grâce à un mystérieux élixir, est devenu un meurtrier parfait. Ses cheveux blancs, ses yeux nyctalopes et son manteau noir effrayent et fascinent. Il parcourt des contrées pittoresques en gagnant sa vie comme chasseur de monstres. En ces temps obscurs, ogres, goules et vampires pullulent, et les magiciens sont des manipulateurs experts. Contre ces menaces, il faut un tueur à gages à la hauteur. Car Geralt est plus qu’un guerrier ou un mage. C’est un Sorceleur. Il est unique. Au cours de ses aventures, il rencontrera une autoritaire mais généreuse prêtresse, un troubadour paillard au grand cœur, et une magicienne capricieuse aux charmes vénéneux. Amis d’un jour, amours d\'une nuit. Mais au bout d

In [622]:
lst_test = []

for x,y in dict_book_avis_per_pseudo.items(): 
    
    for i in y :
        lst_test.append([x,i[0],i[1]])
    
lst_test

[['[Sapkowski, Andrzej] Sorceleur - Saga', 'Le Serial Lecteur', 'joy'],
 ['[Sapkowski, Andrzej] Sorceleur - Saga', 'Walpurgis', 'joy'],
 ['[Sapkowski, Andrzej] Sorceleur - Saga', 'Renan', 'joy'],
 ['[Sapkowski, Andrzej] Sorceleur - Saga', 'Le Serial Lecteur', 'joy'],
 ['[Sapkowski, Andrzej] Sorceleur - Saga', 'Zina', 'joy'],
 ['[Sapkowski, Andrzej] Sorceleur - Saga', 'Sia', 'joy'],
 ['[Sapkowski, Andrzej] Sorceleur - Saga', 'AppleCokes Read', 'joy'],
 ['[Sapkowski, Andrzej] Sorceleur - Saga', 'Sia', 'joy'],
 ['[Sapkowski, Andrzej] Sorceleur - Saga', 'cassie56', 'joy'],
 ['[Sapkowski, Andrzej] Sorceleur - Saga', 'Mademoiselle books', 'joy'],
 ['[Sapkowski, Andrzej] Sorceleur - Saga', 'Esoriak', 'joy'],
 ['[Sapkowski, Andrzej] Sorceleur - Saga', 'Zachanariel', 'joy'],
 ['[Sapkowski, Andrzej] Sorceleur - Saga', 'Labibliogirly', 'joy'],
 ['[Sapkowski, Andrzej] Sorceleur - Saga', 'Winry89', 'joy'],
 ['[Sapkowski, Andrzej] Sorceleur - Saga', 'MahaultMots', 'joy'],
 ['[Sapkowski, Andrzej] Sor

In [623]:
#Transform the dict_book_avis_per_pseudo into DataFrame => df_book_avis_per_pseudo

df_book_avis_per_pseudo = pd.DataFrame(lst_test)
df_book_avis_per_pseudo = df_book_avis_per_pseudo.rename(columns={0:'Book',1:'User',2:'Avis'})
df_book_avis_per_pseudo

Book               User           Avis
0     [Sapkowski, Andrzej] Sorceleur - Saga  Le Serial Lecteur            joy
1     [Sapkowski, Andrzej] Sorceleur - Saga          Walpurgis            joy
2     [Sapkowski, Andrzej] Sorceleur - Saga              Renan            joy
3     [Sapkowski, Andrzej] Sorceleur - Saga  Le Serial Lecteur            joy
4     [Sapkowski, Andrzej] Sorceleur - Saga               Zina            joy
...                                     ...                ...            ...
4673  [Sapkowski, Andrzej] Sorceleur - Saga            Alindra  joyanalytical
4674  [Sapkowski, Andrzej] Sorceleur - Saga           mariiine            joy
4675  [Sapkowski, Andrzej] Sorceleur - Saga         jellybells            joy
4676  [Sapkowski, Andrzej] Sorceleur - Saga               Otsü            joy
4677  [Sapkowski, Andrzej] Sorceleur - Saga         jellybells          anger

[4678 rows x 3 columns]

In [624]:
#Add ddf_book_avis_per_pseudo to MySQL
df_book_avis_per_pseudo.to_sql('df_book_avis_per_pseudo_test', engine, if_exists='replace', index=True)


In [626]:
lst_of_all_books = []
data_profile_url = []

for x,y in df_book_pseudo_lien_and_comments.items():
    
    lst_of_all_books.append(x)
    
    for j in y:
        data_profile_url.append(j[1])



In [627]:
print(lst_of_all_books)
print(len(lst_of_all_books))

['[Sapkowski, Andrzej] Sorceleur - Saga', "[Ivy, Alexandra] Les Gardiens de l'éternité - Saga", '[Feist, Raymond E.] La Guerre de la Faille - Saga', "[Goddyn, Régis] L'Ensorceleur des choses menues", '[Pacat, S.C] Prince Captif - Saga', '[Caldera, Georgia] Les Larmes rouges - Saga', "Qu'est-ce qui ferait le jeu fantastique parfait pour vous?", 'À propos du Doom of Mandos', '[Frost, Jeaniene] Chasseuse de la nuit - Saga', "[Goodkind, Terry] L'Épée de Vérité - Saga", "[Bry, David] Que passe l'hiver", '[Latil-Nicolas, Thibaud] Chevauche-brumes - Saga', '[Brooks, Terry] Shannara - Saga', '[Tolkien, J. R. R.] Le Seigneur des Anneaux - Saga']
14


In [628]:
#print(data_profile_url)
print(len(data_profile_url))

#Keep only unique profile_url
set_unique_profile_url = set(data_profile_url)
print(len(set_unique_profile_url))

#Transform set_unique_profile_url into lst_unique_profile_url
lst_unique_profile_url = list(set_unique_profile_url)

48132
546


In [632]:
#Create a Dict with the sexe, the age and the localisation if available for each user profiles
#WARNING => LONG RUN untill XXXX (~XXmin with 1 to 3 sec time sleep) - 3 min for 546

#CSS Selector for user name => .profile-usertitle-name
#CSS Selector for sexe => .profile-usertitle-name img
#CSS Selector for age and localisation => .profile-usertitle-job
#CSS Selector for #books readed => i.contains(' Livres lus ') .badge   a:contains(' Livres lus ')

#Pattern => 'href="\/profil.*?<strong>.*?<\/strong>'
#Pattern => 'href="\/profil.*?"'
#Pattern => '<.*?>'

dict_users_items = {}
lst_of_users_items_to_add = []
count = 0

for i in lst_unique_profile_url:
    
    url = i
    #print(url)
    html=r.get(url, headers=headers).content
    soup=BeautifulSoup(html)

    user_name = [profile.text for profile in soup.select('.profile-usertitle-name')]
    user_name = ''.join(user_name).strip()
    user_sexe = [profile['alt'] for profile in soup.select('.profile-usertitle-name img')]
    user_age = [profile.text for profile in soup.select('.profile-usertitle-job')]
    user_age = ''.join(user_age).split(',')

    if len(user_age) > 1:
        user_localisation = [user_age[1]]
        user_age = [user_age[0]]

    else : 
        user_localisation = ['null']

    user_reading_status = [profile.text for profile in soup.select("a:contains(' Livres lus ')")]
    user_reading_status = ''.join(user_reading_status).split()
    user_reading_status = [int(user_reading_status[2])]

    lst_of_users_items_to_add = []
    lst_of_users_items_to_add.append([user_sexe,user_age,user_localisation,user_reading_status])

    flat_list = []
    for sublist in lst_of_users_items_to_add:
        for items in sublist:
            for item in items:
                flat_list.append(item)

    dict_users_items[user_name] = flat_list

    count += 1
    print(count)

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
277


In [633]:
#Transform dict_users_items into DataFrame => df_users_items

df_users_items = pd.DataFrame.from_dict(dict_users_items, orient='index')
df_users_items = df_users_items.reset_index()
df_users_items = df_users_items.rename(columns={'index':'Username',0:'Sexe',1:'Age',2:'Localisation',3:'Nb of book read'})
df_users_items

Username                Sexe     Age    Localisation  Nb of book read
0         Sookies               Femme  31 ans          France            550.0
1         Taveera               Femme  33 ans          France            460.0
2    Mitsuki-chan               Femme  30 ans          France              2.0
3       Walpurgis               Femme  36 ans           Rouen           1153.0
4            miki               Femme                    null              0.0
..            ...                 ...     ...             ...              ...
541       Caelina               Femme  30 ans            null           1523.0
542        Lunacy               Femme  28 ans            Lyon            110.0
543        Kassie               Femme  27 ans            null            275.0
544           Sia  Derrière un livre!    null            1952              NaN
545       Fraca14               Femme  56 ans   Québec Canada              0.0

[546 rows x 5 columns]

In [636]:
#Add df_users_items to MySQL
df_users_items.to_sql('df_users_items', engine, if_exists='replace', index=True)

In [637]:
print("c'est gagné")

c'est gagné


In [92]:
#https://medium.com/@chaimgluck1/have-messy-text-data-clean-it-with-simple-lambda-functions-645918fcc2fc

In [599]:
#SET UP API AYLIEN
#Limits 120 hits / minute and 120 000 / month
client = textapi.Client("8819323b", "58c7ab2812ff27dcc7c8bcea8fdb1983")

#Parameters
    #'categories_taxonomy': 'iptc-subjectcode',
    #'categories_id': ['04010002'], => Book
    #'language': ['auto'],
    #'source_locations_country': ['FR'],